# You must adjust the dates in the for loop and then change the string manipulation depending on the year.

In [67]:
import datetime as dt
from lxml import html
from bs4 import BeautifulSoup
import urllib
import sys
import requests
import operator
from datetime import timedelta
import csv
import pandas as pd
import numpy as np
import math

In [68]:
def fill_games_list(games_table,game_list,yesterday):
    for x in games_table:

        if x.find("tbody").findAll("tr")[0].find("a").has_attr('href') and x.find("tbody").findAll("tr")[1].find("a").has_attr('href'):
            
            winner = x.find("tbody").find("tr",{"class":"winner"}).find("a").text
            winner_score = x.find("tbody").find("tr",{"class":"winner"}).find("td",{"class":"right"}).text
            loser = x.find("tbody").find("tr",{"class":"loser"}).find("a").text
            loser_score = x.find("tbody").find("tr",{"class":"loser"}).find("td",{"class":"right"}).text
            home_team =x.find("tbody").findAll("tr")[1].find("a").text
            away_team =x.find("tbody").findAll("tr")[0].find("a").text
            
            for x in [winner, loser, home_team, away_team]:
                if x in ['UCSB',"St. Peter's","St. Joseph's","BYU","Saint Mary's",'UMKC','SIU-Edwardsville','UTSA','UT-Martin','UTEP','LSU','California','Penn','USC','Southern Miss','LIU-Brooklyn','TCU','ETSU','Central Connecticut','Pitt','Detroit','Ole Miss','UIC','UNC','NC State','USC Upstate','UMBC','UMass','UMass-Lowell','UNC Asheville','UConn','VCU','SMU','UCF','UNLV','UNC Wilmington','UNC Greensboro']:
                    x = x.replace("UNC Asheville", "North Carolina-Asheville")
                    x = x.replace("UNC Wilmington", "North Carolina-Wilmington")
                    x = x.replace("UNC Greensboro", "North Carolina-Greensboro")
                    x = x.replace("UNC", "North Carolina")
                    x = x.replace("NC State", "North Carolina State")
                    x = x.replace("USC Upstate", "South Carolina Upstate")
                    x = x.replace("UMBC", "Maryland-Baltimore County")
                    x = x.replace("UMass", "Massachusetts")
                    x = x.replace("UConn", "Connecticut")
                    x = x.replace("VCU", "Virginia Commonwealth")
                    x = x.replace("SMU", "Southern Methodist")
                    x = x.replace("UCF", "Central Florida")
                    x = x.replace("UNLV", "Nevada-Las Vegas")
                    x = x.replace("UIC", "Illinois-Chicago")
                    x = x.replace("Ole Miss", "Mississippi")
                    x = x.replace("Detroit", "Detroit Mercy")
                    x = x.replace("Pitt", "Pittsburgh")
                    x = x.replace("Central Connecticut", "Central Connecticut State")
                    x = x.replace("ETSU", "East Tennessee State")
                    x = x.replace("TCU", "Texas Christian")
                    x = x.replace("LIU-Brooklyn", "Long Island University")
                    x = x.replace("Southern Miss", "Southern Mississippi")
                    x = x.replace("California", "University of California")
                    x = x.replace("USC", "Southern California")
                    x = x.replace("Penn", "Pennsylvania")
                    x = x.replace("LSU", "Louisiana State")
                    x = x.replace("UTEP", "Texas-El Paso")
                    x = x.replace("UT-Martin", "Tennessee-Martin")
                    x = x.replace("UTSA", "Texas-San Antonio")
                    x = x.replace("SIU-Edwardsville", "SIU Edwardsville")
                    x = x.replace("UMKC", "Missouri-Kansas City")
                    x = x.replace("Saint Mary's", "Saint Mary's (CA)")
                    x = x.replace("BYU", "Brigham Young")
                    x = x.replace("St. Joseph's", "Saint Joseph's")
                    x = x.replace("St. Peter's", "Saint Peter's")
                    x = x.replace("UCSB", "UC-Santa Barbara")
                
            game_list.append((yesterday,winner,winner_score,loser,loser_score,home_team,away_team))
        else:
            pass

In [69]:
yesterday = dt.date.today()- timedelta(days=220)
yesterday

datetime.date(2020, 5, 1)

In [102]:
for x in range(205+(365*4),215+(365*3),-1):
        yesterday = dt.date.today()- timedelta(days=x)
        print(yesterday)

2016-05-17
2016-05-18
2016-05-19
2016-05-20
2016-05-21
2016-05-22
2016-05-23
2016-05-24
2016-05-25
2016-05-26
2016-05-27
2016-05-28
2016-05-29
2016-05-30
2016-05-31
2016-06-01
2016-06-02
2016-06-03
2016-06-04
2016-06-05
2016-06-06
2016-06-07
2016-06-08
2016-06-09
2016-06-10
2016-06-11
2016-06-12
2016-06-13
2016-06-14
2016-06-15
2016-06-16
2016-06-17
2016-06-18
2016-06-19
2016-06-20
2016-06-21
2016-06-22
2016-06-23
2016-06-24
2016-06-25
2016-06-26
2016-06-27
2016-06-28
2016-06-29
2016-06-30
2016-07-01
2016-07-02
2016-07-03
2016-07-04
2016-07-05
2016-07-06
2016-07-07
2016-07-08
2016-07-09
2016-07-10
2016-07-11
2016-07-12
2016-07-13
2016-07-14
2016-07-15
2016-07-16
2016-07-17
2016-07-18
2016-07-19
2016-07-20
2016-07-21
2016-07-22
2016-07-23
2016-07-24
2016-07-25
2016-07-26
2016-07-27
2016-07-28
2016-07-29
2016-07-30
2016-07-31
2016-08-01
2016-08-02
2016-08-03
2016-08-04
2016-08-05
2016-08-06
2016-08-07
2016-08-08
2016-08-09
2016-08-10
2016-08-11
2016-08-12
2016-08-13
2016-08-14
2016-08-15

In [103]:
def get_yest_games():
    game_list = []
    for x in range(205+(365*4),215+(365*3),-1):
        yesterday = dt.date.today()- timedelta(days=x)
        if yesterday == dt.date(2020, 1, 20):
            continue
        SR_games = "https://www.sports-reference.com/cbb/boxscores/index.cgi?month="+str(yesterday.month)+"&day="+str(yesterday.day)+"&year="+str(yesterday.year)
        #print(SR_games)
        try:
            games = requests.get(SR_games)
            soup_games = BeautifulSoup(games.content, 'lxml')
            games_table=soup_games.findAll("div",{"class":"game_summary nohover"})
            print(games_table)
            fill_games_list(games_table,game_list,yesterday)
        except:
            print("ERROR!")
    return game_list

In [104]:
def add_ken_pom(teams_dict, KP):

    kenpom = requests.get(KP)
    soup_kenpom = BeautifulSoup(kenpom.content, 'lxml')
    kenpom_table=soup_kenpom.find("table",{"id":"ratings-table"})
    kenpom_table.findAll("tr")[2].findAll("td")[4]

    for x in kenpom_table.findAll("tr"):
        if x.find("a") == None or x.find("td") == None:
            pass
        else:
            team = x.find("a").text
            rank = int(x.find("td").text)
            val = x.findAll("td")[4].text
            if "Merrimack" in team:
                continue
            if "Savannah St" in team:
                continue
            if "Louisiana Lafayette" in team:
                team = "Louisiana"
            if "Fort Wayne" in team:
                team = "Purdue Fort Wayne"
            if "College of Charleston" in team:
                team = "College Charleston"
            teams_dict[team] = {}                       
            teams_dict[team]['Team'] = [team]
            teams_dict[team]['KenPomRank'] = rank
            teams_dict[team]['KenPomVal'] = val

# # This section adds BPI to the teams_dict 

def add_BPI(teams_dict, BP):
    for link in BP:
        r = requests.get(link)
        soup2 = BeautifulSoup(r.content, 'lxml')
        table=soup2.find("table",{"class":"bpi__table"})
        if table is None:
            continue
        for x in table.find("tbody").findAll("tr"):
            if x.find("a") == None or x.find("td") == None:
              pass
            else:
                team = x.find("span",{"class":"team-names"}).text
                BPI_name = x.find("span",{"class":"team-names"}).text
                rank = x.findAll("td")[0].text
                val = x.findAll("td")[6].text
                if "Boston Univ." in team:
                    team = "Boston University"
                if "Long Island University" in team:
                    team = "LIU Brooklyn"
                if "Loyola (Chi)" in team:
                    team = "Loyola Chicago"
                if "Loyola (Chi)" in team:
                    team = "Loyola Chicago"
                if "Loyola (MD)" in team:
                    team = "Loyola MD"
                if "Arkansas St" in team:
                    team = "Arkansas State"
                if "Youngstown St" in team:
                    team = "Youngstown St."
                if "Tarleton" in team:
                    team = "Tarleton St."
                if "Savannah St" in team:
                    continue
                if "Merrimack" in team:
                    continue
                if "Umbc" in team:
                    team = "UMBC"
                if "-" in team or "(" in team or ")" in team:
                    team = team.replace("-", " ")
                    team = team.replace("(", "")
                    team = team.replace(")", "")
                if "é" in team:
                    team = team.replace("é", "e")
                if "NC St" in team:
                    team = team.replace("NC", "North Carolina")
                if "State" in team:
                    team = team.replace("State", "St.")
                if "CSU" in team:
                    team = team.replace("CSU", "Cal St.")
                if "CC" in team:
                    team = team.replace("CC", "Corpus Chris")
                if "Se " in team or "SE " in team or "Mt." in team:
                    team = team.replace("Se", "Southeast")
                    team = team.replace("SE", "Southeastern")
                    team = team.replace("Mt.", "Mount")
                if team in ["Charleston","Seattle U", "UM Kansas City", "Arkansas Little Rock", "Appalachian St", "Georgia St", "North Carolina St.", "Southeastern Missouri St", "San José St", "South Carolina Upstate", "California Baptist", "Detroit Mercy", "McNeese", "Southeast Missouri St", "UT Martin", "Nicholls", "Grambling", "Miami", "Ole Miss", "UConn", "Pennsylvania", "UMass", "UL Monroe", "Omaha", "UIC", "Florida International", "St. Francis BKN", "Hawai'i"]:
                    team = team.replace("Charleston", "College Charleston")
                    team = team.replace("Seattle U", "Seattle")
                    team = team.replace("UM Kansas City", "UMKC")
                    team = team.replace("Arkansas Little Rock", "Little Rock")
                    team = team.replace("Appalachian St", "Appalachian St.")
                    team = team.replace("Georgia St", "Georgia St.")
                    team = team.replace("North Carolina St.", "N.C. State")
                    team = team.replace("San José St", "San Jose St.")
                    team = team.replace(
                        "South Carolina Upstate", "USC Upstate")
                    team = team.replace("California Baptist", "Cal Baptist")
                    team = team.replace("Detroit Mercy", "Detroit")
                    team = team.replace("McNeese", "McNeese St.")
                    team = team.replace(
                        "Southeast Missouri St", "Southeast Missouri St.")
                    team = team.replace(
                        "Southeastern Missouri St", "Southeast Missouri St.")
                    team = team.replace("UT Martin", "Tennessee Martin")
                    team = team.replace("Nicholls", "Nicholls St.")
                    team = team.replace("Grambling", "Grambling St.")
                    team = team.replace("Miami", "Miami FL")
                    team = team.replace("Ole Miss", "Mississippi")
                    team = team.replace("UConn", "Connecticut")
                    team = team.replace("Pennsylvania", "Penn")
                    team = team.replace("UMass", "Massachusetts")
                    team = team.replace("UL Monroe", "Louisiana Monroe")
                    team = team.replace("Omaha", "Nebraska Omaha")
                    team = team.replace("UIC", "Illinois Chicago")
                    team = team.replace("Florida International", "FIU")
                    team = team.replace("St. Francis BKN", "St. Francis NY")
                    team = team.replace("Hawai'i", "Hawaii")

                teams_dict[team]['BPIrank'] = rank
                teams_dict[team]['BPIval'] = val
                teams_dict[team]['Team'].append(BPI_name)

# #  This Section brings in SRS to teams

def add_sports_ref(teams_dict, SRS):
    srs = requests.get(SRS)
    soup_srs = BeautifulSoup(srs.content, 'lxml')
    srs_table=soup_srs.find("table",{"id":"ratings"})

    for x in srs_table.find("tbody").findAll("tr"):
        if x.find("a") == None or x.findAll("td")[13] == None:
            pass
        else:
            team = x.find("a").text
            SRS_name = x.find("a").text
            srs_val = x.findAll("td")[13].text
            sos_val = x.findAll("td")[10].text
            o_eff = x.findAll("td")[14].text
            d_eff = x.findAll("td")[15].text
            ppg = x.findAll("td")[5].text
            papg = x.findAll("td")[6].text
            if "Savannah St" in team:
                continue
            if "Merrimack" in team:
                continue
            if "State" in team:
                team = team.replace("State", "St.")
            if "University" in team:
                team = team.replace("University ", "")
            if "of " in team:
                team = team.replace("of ", "")
            if "-" in team or "(" in team or ")" in team:
                team = team.replace("-", " ")
                team = team.replace("(", "")
                team = team.replace(")", "")
            if team in ["Cal St. Long Beach", "North Carolina St.", "North Carolina Asheville", "South Carolina Upstate", "Albany NY", "Prairie View", "Missouri Kansas City", "Long Island University", "Massachusetts Lowell", "Maryland Baltimore County", "North Carolina Wilmington", "Saint Francis PA", "Grambling", "Central Connecticut St.", "Detroit Mercy", "Texas A&M Corpus Christi", "Omaha", "Texas Arlington", "Florida International", "California Baptist", "Bowling Green St.", "Texas San Antonio", "Texas Rio Grande Valley", "Texas El Paso", "Alabama Birmingham", "Southern Mississippi", "Citadel", "North Carolina Greensboro", "Southern Methodist", "Southern California", "Pennsylvania", "Nevada Las Vegas", "St. John's NY", "Loyola IL", "Brigham Young", "Virginia Commonwealth", "Central Florida", "Louisiana St.", "Texas Christian", "Saint Mary's CA"]:
                team = team.replace("Cal St. Long Beach", "Long Beach St.")
                team = team.replace("North Carolina St.", "N.C. State")
                team = team.replace(
                    "North Carolina Asheville", "UNC Asheville")
                team = team.replace("South Carolina Upstate", "USC Upstate")
                team = team.replace("Albany NY", "Albany")
                team = team.replace("Prairie View", "Prairie View A&M")
                team = team.replace("Missouri Kansas City", "UMKC")
                team = team.replace("Long Island University", "LIU Brooklyn")
                team = team.replace("Massachusetts Lowell", "UMass Lowell")
                team = team.replace("Maryland Baltimore County", "UMBC")
                team = team.replace(
                    "North Carolina Wilmington", "UNC Wilmington")
                team = team.replace("Saint Francis PA", "St. Francis PA")
                team = team.replace("Grambling", "Grambling St.")
                team = team.replace(
                    "Central Connecticut St.", "Central Connecticut")
                team = team.replace("Detroit Mercy", "Detroit")
                team = team.replace(
                    "Texas A&M Corpus Christi", "Texas A&M Corpus Chris")
                team = team.replace("Omaha", "Nebraska Omaha")
                team = team.replace("Texas Arlington", "UT Arlington")
                team = team.replace("Florida International", "FIU")
                team = team.replace("California Baptist", "Cal Baptist")
                team = team.replace("Bowling Green St.", "Bowling Green")
                team = team.replace("Texas San Antonio", "UTSA")
                team = team.replace(
                    "Texas Rio Grande Valley", "UT Rio Grande Valley")
                team = team.replace("Texas El Paso", "UTEP")
                team = team.replace("Alabama Birmingham", "UAB")
                team = team.replace("Southern Mississippi", "Southern Miss")
                team = team.replace("Citadel", "The Citadel")
                team = team.replace(
                    "North Carolina Greensboro", "UNC Greensboro")
                team = team.replace("Southern Methodist", "SMU")
                team = team.replace("Southern California", "USC")
                team = team.replace("Pennsylvania", "Penn")
                team = team.replace("Nevada Las Vegas", "UNLV")
                team = team.replace("St. John's NY", "St. John's")
                team = team.replace("Loyola IL", "Loyola Chicago")
                team = team.replace("Brigham Young", "BYU")
                team = team.replace("Virginia Commonwealth", "VCU")
                team = team.replace("Central Florida", "UCF")
                team = team.replace("Louisiana St.", "LSU")
                team = team.replace("Texas Christian", "TCU")
                team = team.replace("Saint Mary's CA", "Saint Mary's")

            teams_dict[team]['SRS'] = srs_val
            teams_dict[team]['SOS'] = sos_val
            teams_dict[team]['o_eff'] = o_eff
            teams_dict[team]['d_eff'] = d_eff
            teams_dict[team]['ppg'] = ppg
            teams_dict[team]['papg'] = papg
            teams_dict[team]['Team'] =SRS_name

def add_advanced(teams_dict):
    SR_ratings_team = "https://www.sports-reference.com/cbb/seasons/2017-advanced-school-stats.html"
    SR_ratings_opp = "https://www.sports-reference.com/cbb/seasons/2017-advanced-opponent-stats.html"
    
    team_ratings = requests.get(SR_ratings_team)
    team_soup_ratings = BeautifulSoup(team_ratings.content, 'lxml')
    team_ratings_table=team_soup_ratings.find("table",{"id":"adv_school_stats"})
    teams = team_ratings_table.find("tbody").findAll("tr")
    
    opp_ratings = requests.get(SR_ratings_opp)
    opp_soup_ratings = BeautifulSoup(opp_ratings.content, 'lxml')
    opp_ratings_table=opp_soup_ratings.find("table",{"id":"adv_opp_stats"})
    opps = opp_ratings_table.find("tbody").findAll("tr")
    
    for x in teams:
        if x.find("a") == None or x.findAll("td")[16] == None:
            pass
        else:
            team = x.find('a').text
            pace = x.findAll('td')[20].text
            Three_Par = x.findAll('td')[23].text
            TS = x.findAll('td')[24].text
            Tov = x.findAll('td')[30].text
            if "Savannah St" in team:
                continue
            if "Merrimack" in team:
                continue
            if "State" in team:
                team = team.replace("State", "St.")
            if "University" in team:
                team = team.replace("University ", "")
            if "of " in team:
                team = team.replace("of ", "")
            if "-" in team or "(" in team or ")" in team:
                team = team.replace("-", " ")
                team = team.replace("(", "")
                team = team.replace(")", "")
            if team in ["North Carolina St.", "Cal St. Long Beach", "North Carolina Asheville", "South Carolina Upstate", "Albany NY", "Prairie View", "Missouri Kansas City", "Long Island University", "Massachusetts Lowell", "Maryland Baltimore County", "North Carolina Wilmington", "Saint Francis PA", "Grambling", "Central Connecticut St.", "Detroit Mercy", "Texas A&M Corpus Christi", "Omaha", "Texas Arlington", "Florida International", "California Baptist", "Bowling Green St.", "Texas San Antonio", "Texas Rio Grande Valley", "Texas El Paso", "Alabama Birmingham", "Southern Mississippi", "Citadel", "North Carolina Greensboro", "Southern Methodist", "Southern California", "Pennsylvania", "Nevada Las Vegas", "St. John's NY", "Loyola IL", "Brigham Young", "Virginia Commonwealth", "Central Florida", "Louisiana St.", "Texas Christian", "Saint Mary's CA"]:
                team = team.replace("Cal St. Long Beach", "Long Beach St.")
                team = team.replace("North Carolina St.", "N.C. State")
                team = team.replace(
                    "North Carolina Asheville", "UNC Asheville")
                team = team.replace("South Carolina Upstate", "USC Upstate")
                team = team.replace("Albany NY", "Albany")
                team = team.replace("Prairie View", "Prairie View A&M")
                team = team.replace("Missouri Kansas City", "UMKC")
                team = team.replace("Long Island University", "LIU Brooklyn")
                team = team.replace("Massachusetts Lowell", "UMass Lowell")
                team = team.replace("Maryland Baltimore County", "UMBC")
                team = team.replace(
                    "North Carolina Wilmington", "UNC Wilmington")
                team = team.replace("Saint Francis PA", "St. Francis PA")
                team = team.replace("Grambling", "Grambling St.")
                team = team.replace(
                    "Central Connecticut St.", "Central Connecticut")
                team = team.replace("Detroit Mercy", "Detroit")
                team = team.replace(
                    "Texas A&M Corpus Christi", "Texas A&M Corpus Chris")
                team = team.replace("Omaha", "Nebraska Omaha")
                team = team.replace("Texas Arlington", "UT Arlington")
                team = team.replace("Florida International", "FIU")
                team = team.replace("California Baptist", "Cal Baptist")
                team = team.replace("Bowling Green St.", "Bowling Green")
                team = team.replace("Texas San Antonio", "UTSA")
                team = team.replace(
                    "Texas Rio Grande Valley", "UT Rio Grande Valley")
                team = team.replace("Texas El Paso", "UTEP")
                team = team.replace("Alabama Birmingham", "UAB")
                team = team.replace("Southern Mississippi", "Southern Miss")
                team = team.replace("Citadel", "The Citadel")
                team = team.replace(
                    "North Carolina Greensboro", "UNC Greensboro")
                team = team.replace("Southern Methodist", "SMU")
                team = team.replace("Southern California", "USC")
                team = team.replace("Pennsylvania", "Penn")
                team = team.replace("Nevada Las Vegas", "UNLV")
                team = team.replace("St. John's NY", "St. John's")
                team = team.replace("Loyola IL", "Loyola Chicago")
                team = team.replace("Brigham Young", "BYU")
                team = team.replace("Virginia Commonwealth", "VCU")
                team = team.replace("Central Florida", "UCF")
                team = team.replace("Louisiana St.", "LSU")
                team = team.replace("Texas Christian", "TCU")
                team = team.replace("Saint Mary's CA", "Saint Mary's")

            teams_dict[team]['Pace'] = pace
            teams_dict[team]['Three_Par'] = Three_Par
            teams_dict[team]['True_Shoot'] = TS
            teams_dict[team]['Tov'] = Tov
    for x in opps:
        if x.find("a") == None or x.findAll("td")[16] == None:
            pass
        else:
            team = x.find('a').text
            Three_Par = x.findAll('td')[23].text
            TS = x.findAll('td')[24].text
            Tov = x.findAll('td')[30].text

            if "Savannah St" in team:
                continue
            if "Merrimack" in team:
                continue
            if "State" in team:
                team = team.replace("State", "St.")
            if "University" in team:
                team = team.replace("University ", "")
            if "of " in team:
                team = team.replace("of ", "")
            if "-" in team or "(" in team or ")" in team:
                team = team.replace("-", " ")
                team = team.replace("(", "")
                team = team.replace(")", "")
            if team in ["North Carolina St.", "Cal St. Long Beach", "North Carolina Asheville", "South Carolina Upstate", "Albany NY", "Prairie View", "Missouri Kansas City", "Long Island University", "Massachusetts Lowell", "Maryland Baltimore County", "North Carolina Wilmington", "Saint Francis PA", "Grambling", "Central Connecticut St.", "Detroit Mercy", "Texas A&M Corpus Christi", "Omaha", "Texas Arlington", "Florida International", "California Baptist", "Bowling Green St.", "Texas San Antonio", "Texas Rio Grande Valley", "Texas El Paso", "Alabama Birmingham", "Southern Mississippi", "Citadel", "North Carolina Greensboro", "Southern Methodist", "Southern California", "Pennsylvania", "Nevada Las Vegas", "St. John's NY", "Loyola IL", "Brigham Young", "Virginia Commonwealth", "Central Florida", "Louisiana St.", "Texas Christian", "Saint Mary's CA"]:
                team = team.replace("Cal St. Long Beach", "Long Beach St.")
                team = team.replace("North Carolina St.", "N.C. State")
                team = team.replace(
                    "North Carolina Asheville", "UNC Asheville")
                team = team.replace("South Carolina Upstate", "USC Upstate")
                team = team.replace("Albany NY", "Albany")
                team = team.replace("Prairie View", "Prairie View A&M")
                team = team.replace("Missouri Kansas City", "UMKC")
                team = team.replace("Long Island University", "LIU Brooklyn")
                team = team.replace("Massachusetts Lowell", "UMass Lowell")
                team = team.replace("Maryland Baltimore County", "UMBC")
                team = team.replace(
                    "North Carolina Wilmington", "UNC Wilmington")
                team = team.replace("Saint Francis PA", "St. Francis PA")
                team = team.replace("Grambling", "Grambling St.")
                team = team.replace(
                    "Central Connecticut St.", "Central Connecticut")
                team = team.replace("Detroit Mercy", "Detroit")
                team = team.replace(
                    "Texas A&M Corpus Christi", "Texas A&M Corpus Chris")
                team = team.replace("Omaha", "Nebraska Omaha")
                team = team.replace("Texas Arlington", "UT Arlington")
                team = team.replace("Florida International", "FIU")
                team = team.replace("California Baptist", "Cal Baptist")
                team = team.replace("Bowling Green St.", "Bowling Green")
                team = team.replace("Texas San Antonio", "UTSA")
                team = team.replace(
                    "Texas Rio Grande Valley", "UT Rio Grande Valley")
                team = team.replace("Texas El Paso", "UTEP")
                team = team.replace("Alabama Birmingham", "UAB")
                team = team.replace("Southern Mississippi", "Southern Miss")
                team = team.replace("Citadel", "The Citadel")
                team = team.replace(
                    "North Carolina Greensboro", "UNC Greensboro")
                team = team.replace("Southern Methodist", "SMU")
                team = team.replace("Southern California", "USC")
                team = team.replace("Pennsylvania", "Penn")
                team = team.replace("Nevada Las Vegas", "UNLV")
                team = team.replace("St. John's NY", "St. John's")
                team = team.replace("Loyola IL", "Loyola Chicago")
                team = team.replace("Brigham Young", "BYU")
                team = team.replace("Virginia Commonwealth", "VCU")
                team = team.replace("Central Florida", "UCF")
                team = team.replace("Louisiana St.", "LSU")
                team = team.replace("Texas Christian", "TCU")
                team = team.replace("Saint Mary's CA", "Saint Mary's")
            
            teams_dict[team]['Opp_Three_Par'] = Three_Par
            teams_dict[team]['Opp_True_Shoot'] = TS
            teams_dict[team]['Opp_Tov'] = Tov

def formatting(teams_dict):
    for x in teams_dict.keys():
        teams_dict[x]['record_date'] = dt.datetime.now()   
    teams_list = []
    sorted_teams_dict = sorted(teams_dict.items(), key=operator.itemgetter(0))
    for x,y in sorted_teams_dict:
        teams_list.append(y)
    return teams_list

def get_teams():
    teams = {}
    KP = 'https://kenpom.com/index.php?y=2017'
    BP = []
    for x in range(1,16):
        BP.append('http://www.espn.com/mens-college-basketball/bpi/_/season/2017/view/bpi/page/' + str(x))
    SRS = "https://www.sports-reference.com/cbb/seasons/2017-ratings.html"
    
    add_ken_pom(teams, KP)
    add_BPI(teams, BP)
    add_sports_ref(teams, SRS)
    add_advanced(teams)


    teams= formatting(teams)
    return teams

In [105]:
latest_stats = get_teams()
latest_stats = pd.DataFrame(latest_stats)
#latest_stats = latest_stats[['Team','KenPomVal','BPIval','SRS']]

In [106]:
latest_stats

Team  KenPomRank KenPomVal BPIrank BPIval     SRS SOS  \
0    Abilene Christian         298    -11.86     312   -8.8  -11.86       
1            Air Force         222     -5.22     266   -5.4   -3.06       
2                Akron         100     +6.10      84    5.0    3.59       
3              Alabama          56    +13.08      58    7.8   11.29       
4          Alabama A&M         351    -30.34     351  -19.2  -26.99       
..                 ...         ...       ...     ...    ...     ...  ..   
345       Wright State         164     +0.34     154    0.7   -1.02       
346            Wyoming         127     +2.78     190   -1.1    2.83       
347             Xavier          31    +16.70      33   10.4   14.80       
348               Yale         151     +1.01     136    1.6    0.21       
349   Youngstown State         282    -10.29     289   -6.9   -9.75       

      o_eff   d_eff   ppg  papg  Pace Three_Par True_Shoot   Tov  \
0     93.28  108.42  69.3  71.5  68.0      .354       .554  18.5   
1    104.03  107.14  73.1  75.1  68.9      .388       .544  15.0   
2    110.56  103.77  77.0  70.8  68.0      .484       .580  15.0   
3    105.39   88.25  68.5  64.7  67.4      .372       .515  17.3   
4     86.44  124.44  61.9  77.8  65.4      .289       .487  17.3   
..      ...     ...   ...   ...   ...       ...        ...   ...   
345  104.43  104.32  77.0  72.4  71.6      .412       .571  18.0   
346  103.83   98.47  77.9  74.6  74.0      .466       .555  15.8   
347  115.94   93.35  74.6  71.3  68.2      .361       .552  15.7   
348  103.87  102.45  74.2  69.9  68.2      .354       .564  16.5   
349   98.78  110.27  76.9  82.4  73.7      .336       .520  13.9   

    Opp_Three_Par Opp_True_Shoot Opp_Tov                record_date  
0            .373           .553    18.5 2020-12-07 16:27:03.798463  
1            .467           .570    15.8 2020-12-07 16:27:03.798463  
2            .332           .536    14.9 2020-12-07 16:27:03.798463  
3            .340           .500    17.3 2020-12-07 16:27:03.798463  
4            .341           .563    11.8 2020-12-07 16:27:03.798463  
..            ...            ...     ...                        ...  
345          .393           .543    17.8 2020-12-07 16:27:03.798463  
346          .348           .503    14.0 2020-12-07 16:27:03.798463  
347          .395           .546    15.5 2020-12-07 16:27:03.797467  
348          .382           .520    14.9 2020-12-07 16:27:03.798463  
349          .362           .552    14.1 2020-12-07 16:27:03.798463  

[350 rows x 19 columns]

In [107]:
games1 = get_yest_games()

[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[]
[<div class="game_summary nohover">
<table class="teams">
<tbody>
<tr class="loser">
<td><a href="/cbb/schools/marist/2017.html">Marist</a></td>
<td class="right">49</td>
<td class="right gamelink">
<a href="/cbb/boxscores/2016-11-11-duke.html">Final</a>
</td>
</tr>
<tr class="winner">
<td><a href="/cbb/schools/duke/2017.html">Duke</a><span class="pollrank"> (1) </span></td>
<td class="right">94</td>
<td class="right"> 
			</td>
</tr>
</tbody>
</table>
</div>, <

[<div class="game_summary nohover">
<table class="teams">
<tbody>
<tr class="loser">
<td><a href="/cbb/schools/grand-canyon/2017.html">Grand Canyon</a></td>
<td class="right">61</td>
<td class="right gamelink">
<a href="/cbb/boxscores/2016-11-12-duke.html">Final</a>
</td>
</tr>
<tr class="winner">
<td><a href="/cbb/schools/duke/2017.html">Duke</a><span class="pollrank"> (1) </span></td>
<td class="right">96</td>
<td class="right"> 
			</td>
</tr>
</tbody>
</table>
</div>, <div class="game_summary nohover">
<table class="teams">
<tbody>
<tr class="loser">
<td><a href="/cbb/schools/akron/2017.html">Akron</a></td>
<td class="right">82</td>
<td class="right gamelink">
<a href="/cbb/boxscores/2016-11-12-youngstown-state.html">Final</a>
</td>
</tr>
<tr class="winner">
<td><a href="/cbb/schools/youngstown-state/2017.html">Youngstown State</a></td>
<td class="right">90</td>
<td class="right"> 
			</td>
</tr>
</tbody>
</table>
</div>, <div class="game_summary nohover">
<table class="teams">
<tb

[<div class="game_summary nohover">
<table class="teams">
<tbody>
<tr class="loser">
<td><a href="/cbb/schools/canisius/2017.html">Canisius</a></td>
<td class="right">69</td>
<td class="right gamelink">
<a href="/cbb/boxscores/2016-11-13-kentucky.html">Final</a>
</td>
</tr>
<tr class="winner">
<td><a href="/cbb/schools/kentucky/2017.html">Kentucky</a><span class="pollrank"> (2) </span></td>
<td class="right">93</td>
<td class="right"> 
			</td>
</tr>
</tbody>
</table>
</div>, <div class="game_summary nohover">
<table class="teams">
<tbody>
<tr class="loser">
<td><a href="/cbb/schools/chattanooga/2017.html">Chattanooga</a></td>
<td class="right">57</td>
<td class="right gamelink">
<a href="/cbb/boxscores/2016-11-13-north-carolina.html">Final</a>
</td>
</tr>
<tr class="winner">
<td><a href="/cbb/schools/north-carolina/2017.html">UNC</a><span class="pollrank"> (6) </span></td>
<td class="right">97</td>
<td class="right"> 
			</td>
</tr>
</tbody>
</table>
</div>, <div class="game_summary n

[<div class="game_summary nohover">
<table class="teams">
<tbody>
<tr class="winner">
<td><a href="/cbb/schools/villanova/2017.html">Villanova</a><span class="pollrank"> (3) </span></td>
<td class="right">79</td>
<td class="right gamelink">
<a href="/cbb/boxscores/2016-11-14-purdue.html">Final</a>
</td>
</tr>
<tr class="loser">
<td><a href="/cbb/schools/purdue/2017.html">Purdue</a><span class="pollrank"> (15) </span></td>
<td class="right">76</td>
<td class="right"> 
			</td>
</tr>
</tbody>
</table>
</div>, <div class="game_summary nohover">
<table class="teams">
<tbody>
<tr class="loser">
<td><a href="/cbb/schools/buffalo/2017.html">Buffalo</a></td>
<td class="right">53</td>
<td class="right gamelink">
<a href="/cbb/boxscores/2016-11-14-xavier.html">Final</a>
</td>
</tr>
<tr class="winner">
<td><a href="/cbb/schools/xavier/2017.html">Xavier</a><span class="pollrank"> (11) </span></td>
<td class="right">86</td>
<td class="right"> 
			</td>
</tr>
</tbody>
</table>
</div>, <div class="ga

[<div class="game_summary nohover">
<table class="teams">
<tbody>
<tr class="loser">
<td><a href="/cbb/schools/duke/2017.html">Duke</a><span class="pollrank"> (1) </span></td>
<td class="right">75</td>
<td class="right gamelink">
<a href="/cbb/boxscores/2016-11-15-kansas.html">Final</a>
</td>
</tr>
<tr class="winner">
<td><a href="/cbb/schools/kansas/2017.html">Kansas</a><span class="pollrank"> (7) </span></td>
<td class="right">77</td>
<td class="right"> 
			</td>
</tr>
</tbody>
</table>
</div>, <div class="game_summary nohover">
<table class="teams">
<tbody>
<tr class="winner">
<td><a href="/cbb/schools/kentucky/2017.html">Kentucky</a><span class="pollrank"> (2) </span></td>
<td class="right">69</td>
<td class="right gamelink">
<a href="/cbb/boxscores/2016-11-15-michigan-state.html">Final</a>
</td>
</tr>
<tr class="loser">
<td><a href="/cbb/schools/michigan-state/2017.html">Michigan State</a><span class="pollrank"> (13) </span></td>
<td class="right">48</td>
<td class="right"> 
			</

...

[<div class="game_summary nohover">
<table class="teams">
<tbody>
<tr class="loser">
<td><a href="/cbb/schools/california-davis/2017.html">UC-Davis</a><span class="pollrank"> (16) </span></td>
<td class="right">62</td>
<td class="right gamelink">
<a href="/cbb/boxscores/2017-03-17-kansas.html">Final</a>
</td>
</tr>
<tr class="winner">
<td><a href="/cbb/schools/kansas/2017.html">Kansas</a><span class="pollrank"> (1) </span></td>
<td class="right">100</td>
<td class="right"> 
			</td>
</tr>
<tr><td class="desc" colspan="3">NCAA, Midwest - First Round</td></tr>
</tbody>
</table>
</div>, <div class="game_summary nohover">
<table class="teams">
<tbody>
<tr class="loser">
<td><a href="/cbb/schools/texas-southern/2017.html">Texas Southern</a><span class="pollrank"> (16) </span></td>
<td class="right">64</td>
<td class="right gamelink">
<a href="/cbb/boxscores/2017-03-17-north-carolina.html">Final</a>
</td>
</tr>
<tr class="winner">
<td><a href="/cbb/schools/north-carolina/2017.html">UNC</a><s

[<div class="game_summary nohover">
<table class="teams">
<tbody>
<tr class="loser">
<td><a href="/cbb/schools/northwestern/2017.html">Northwestern</a><span class="pollrank"> (8) </span></td>
<td class="right">73</td>
<td class="right gamelink">
<a href="/cbb/boxscores/2017-03-18-gonzaga.html">Final</a>
</td>
</tr>
<tr class="winner">
<td><a href="/cbb/schools/gonzaga/2017.html">Gonzaga</a><span class="pollrank"> (1) </span></td>
<td class="right">79</td>
<td class="right"> 
			</td>
</tr>
<tr><td class="desc" colspan="3">NCAA, West - Second Round</td></tr>
</tbody>
</table>
</div>, <div class="game_summary nohover">
<table class="teams">
<tbody>
<tr class="winner">
<td><a href="/cbb/schools/wisconsin/2017.html">Wisconsin</a><span class="pollrank"> (8) </span></td>
<td class="right">65</td>
<td class="right gamelink">
<a href="/cbb/boxscores/2017-03-18-villanova.html">Final</a>
</td>
</tr>
<tr class="loser">
<td><a href="/cbb/schools/villanova/2017.html">Villanova</a><span class="pollr

[<div class="game_summary nohover">
<table class="teams">
<tbody>
<tr class="loser">
<td><a href="/cbb/schools/akron/2017.html">Akron</a></td>
<td class="right">69</td>
<td class="right gamelink">
<a href="/cbb/boxscores/2017-03-20-texas-arlington.html">Final</a>
</td>
</tr>
<tr class="winner">
<td><a href="/cbb/schools/texas-arlington/2017.html">Texas-Arlington</a></td>
<td class="right">85</td>
<td class="right"> 
			</td>
</tr>
<tr><td class="desc" colspan="3">NIT</td></tr>
</tbody>
</table>
</div>, <div class="game_summary nohover">
<table class="teams">
<tbody>
<tr class="loser">
<td><a href="/cbb/schools/boise-state/2017.html">Boise State</a></td>
<td class="right">56</td>
<td class="right gamelink">
<a href="/cbb/boxscores/2017-03-20-illinois.html">Final</a>
</td>
</tr>
<tr class="winner">
<td><a href="/cbb/schools/illinois/2017.html">Illinois</a></td>
<td class="right">71</td>
<td class="right"> 
			</td>
</tr>
<tr><td class="desc" colspan="3">NIT</td></tr>
</tbody>
</table>
</

[<div class="game_summary nohover">
<table class="teams">
<tbody>
<tr class="loser">
<td><a href="/cbb/schools/purdue/2017.html">Purdue</a><span class="pollrank"> (4) </span></td>
<td class="right">66</td>
<td class="right gamelink">
<a href="/cbb/boxscores/2017-03-23-kansas.html">Final</a>
</td>
</tr>
<tr class="winner">
<td><a href="/cbb/schools/kansas/2017.html">Kansas</a><span class="pollrank"> (1) </span></td>
<td class="right">98</td>
<td class="right"> 
			</td>
</tr>
<tr><td class="desc" colspan="3">NCAA, Midwest - Regional Semifinal</td></tr>
</tbody>
</table>
</div>, <div class="game_summary nohover">
<table class="teams">
<tbody>
<tr class="loser">
<td><a href="/cbb/schools/west-virginia/2017.html">West Virginia</a><span class="pollrank"> (4) </span></td>
<td class="right">58</td>
<td class="right gamelink">
<a href="/cbb/boxscores/2017-03-23-gonzaga.html">Final</a>
</td>
</tr>
<tr class="winner">
<td><a href="/cbb/schools/gonzaga/2017.html">Gonzaga</a><span class="pollrank"

[<div class="game_summary nohover">
<table class="teams">
<tbody>
<tr class="loser">
<td><a href="/cbb/schools/wyoming/2017.html">Wyoming</a></td>
<td class="right">81</td>
<td class="right gamelink">
<a href="/cbb/boxscores/2017-03-27-coastal-carolina.html">Final</a>
</td>
</tr>
<tr class="winner">
<td><a href="/cbb/schools/coastal-carolina/2017.html">Coastal Carolina</a></td>
<td class="right">91</td>
<td class="right"> 
			</td>
</tr>
<tr><td class="desc" colspan="3">CBI</td></tr>
</tbody>
</table>
</div>]
[<div class="game_summary nohover">
<table class="teams">
<tbody>
<tr class="loser">
<td><a href="/cbb/schools/cal-state-bakersfield/2017.html">Cal State Bakersfield</a></td>
<td class="right">61</td>
<td class="right gamelink">
<a href="/cbb/boxscores/2017-03-28-georgia-tech.html">Final</a>
</td>
</tr>
<tr class="winner">
<td><a href="/cbb/schools/georgia-tech/2017.html">Georgia Tech</a></td>
<td class="right">76</td>
<td class="right"> 
			</td>
</tr>
<tr><td class="desc" colspa

In [108]:
games = pd.DataFrame(games1,columns =['Date','Winner','Win_Score','Loser','Lose_Score','Home','Away'])

In [109]:
games

Date       Winner Win_Score                     Loser Lose_Score  \
0     2016-11-11         Duke        94                    Marist         49   
1     2016-11-11     Kentucky        87         Stephen F. Austin         64   
2     2016-11-11      Indiana       103                    Kansas         99   
3     2016-11-11    Villanova        88                 Lafayette         48   
4     2016-11-11       Oregon        91                      Army         77   
...          ...          ...       ...                       ...        ...   
5530  2017-03-31      Wyoming        83          Coastal Carolina         59   
5531  2017-03-31  St. Peter's        62  Texas A&M-Corpus Christi         61   
5532  2017-04-01          UNC        77                    Oregon         76   
5533  2017-04-01      Gonzaga        77            South Carolina         73   
5534  2017-04-03          UNC        71                   Gonzaga         65   

                          Home               Away  
0                         Duke             Marist  
1                     Kentucky  Stephen F. Austin  
2                       Kansas            Indiana  
3                    Villanova          Lafayette  
4                       Oregon               Army  
...                        ...                ...  
5530                   Wyoming   Coastal Carolina  
5531  Texas A&M-Corpus Christi        St. Peter's  
5532                       UNC             Oregon  
5533                   Gonzaga     South Carolina  
5534                       UNC            Gonzaga  

[5535 rows x 7 columns]

In [110]:
games['Winner'] = np.where(games['Winner']=="Ole Miss","Mississippi",games['Winner'])
games['Winner'] = np.where(games['Winner']=="UCSB","UC-Santa Barbara",games['Winner'])
games['Winner'] = np.where(games['Winner']=="UMass-Lowell","Massachusetts-Lowell",games['Winner'])
games['Winner'] = np.where(games['Winner']=="UMass","Massachusetts",games['Winner'])
games['Winner'] = np.where(games['Winner']=="UIC","Illinois-Chicago",games['Winner'])
games['Winner'] = np.where(games['Winner']=="UConn","Connecticut",games['Winner'])
games['Winner'] = np.where(games['Winner']=="Saint Mary's","Saint Mary's (CA)",games['Winner'])
games['Winner'] = np.where(games['Winner']=="VCU","Virginia Commonwealth",games['Winner'])
games['Winner'] = np.where(games['Winner']=="UMKC","Missouri-Kansas City",games['Winner'])
games['Winner'] = np.where(games['Winner']=="St. Joseph's","Saint Joseph's",games['Winner'])
games['Winner'] = np.where(games['Winner']=="BYU","Brigham Young",games['Winner'])
games['Winner'] = np.where(games['Winner']=="UNC","North Carolina",games['Winner'])
games['Winner'] = np.where(games['Winner']=="UTSA","Texas-San Antonio",games['Winner'])
games['Winner'] = np.where(games['Winner']=="Pitt","Pittsburgh",games['Winner'])
games['Winner'] = np.where(games['Winner']=="ETSU","East Tennessee State",games['Winner'])
games['Winner'] = np.where(games['Winner']=="UT-Martin","Tennessee-Martin",games['Winner'])
games['Winner'] = np.where(games['Winner']=="Penn","Pennsylvania",games['Winner'])
games['Winner'] = np.where(games['Winner']=="California","University of California",games['Winner'])
games['Winner'] = np.where(games['Winner']=="USC","Southern California",games['Winner'])
games['Winner'] = np.where(games['Winner']=="UTEP","Texas-El Paso",games['Winner'])
games['Winner'] = np.where(games['Winner']=="UNC Asheville","North Carolina-Asheville",games['Winner'])
games['Winner'] = np.where(games['Winner']=="UNC Greensboro","North Carolina-Greensboro",games['Winner'])
games['Winner'] = np.where(games['Winner']=="UNC Wilmington","North Carolina-Wilmington",games['Winner'])
games['Winner'] = np.where(games['Winner']=="UNLV","Nevada-Las Vegas",games['Winner'])
games['Winner'] = np.where(games['Winner']=="SMU","Southern Methodist",games['Winner'])
games['Winner'] = np.where(games['Winner']=="LIU","Long Island University",games['Winner'])
games['Winner'] = np.where(games['Winner']=="NC State","North Carolina State",games['Winner'])
games['Winner'] = np.where(games['Winner']=="UCF","Central Florida",games['Winner'])
games['Winner'] = np.where(games['Winner']=="Southern Miss","Southern Mississippi",games['Winner'])
games['Winner'] = np.where(games['Winner']=="LSU","Louisiana State",games['Winner'])
games['Winner'] = np.where(games['Winner']=="UIC","Illinois-Chicago",games['Winner'])
games['Winner'] = np.where(games['Winner']=="UMBC","Maryland-Baltimore County",games['Winner'])

In [111]:
games['Loser'] = np.where(games['Loser']=="Ole Miss","Mississippi",games['Loser'])
games['Loser'] = np.where(games['Loser']=="UCSB","UC-Santa Barbara",games['Loser'])
games['Loser'] = np.where(games['Loser']=="UMass-Lowell","Massachusetts-Lowell",games['Loser'])
games['Loser'] = np.where(games['Loser']=="UMass","Massachusetts",games['Loser'])
games['Loser'] = np.where(games['Loser']=="UIC","Illinois-Chicago",games['Loser'])
games['Loser'] = np.where(games['Loser']=="UConn","Connecticut",games['Loser'])
games['Loser'] = np.where(games['Loser']=="Saint Mary's","Saint Mary's (CA)",games['Loser'])
games['Loser'] = np.where(games['Loser']=="VCU","Virginia Commonwealth",games['Loser'])
games['Loser'] = np.where(games['Loser']=="UMKC","Missouri-Kansas City",games['Loser'])
games['Loser'] = np.where(games['Loser']=="St. Joseph's","Saint Joseph's",games['Loser'])
games['Loser'] = np.where(games['Loser']=="BYU","Brigham Young",games['Loser'])
games['Loser'] = np.where(games['Loser']=="UNC","North Carolina",games['Loser'])
games['Loser'] = np.where(games['Loser']=="UTSA","Texas-San Antonio",games['Loser'])
games['Loser'] = np.where(games['Loser']=="Pitt","Pittsburgh",games['Loser'])
games['Loser'] = np.where(games['Loser']=="ETSU","East Tennessee State",games['Loser'])
games['Loser'] = np.where(games['Loser']=="UT-Martin","Tennessee-Martin",games['Loser'])
games['Loser'] = np.where(games['Loser']=="Penn","Pennsylvania",games['Loser'])
games['Loser'] = np.where(games['Loser']=="California","University of California",games['Loser'])
games['Loser'] = np.where(games['Loser']=="USC","Southern California",games['Loser'])
games['Loser'] = np.where(games['Loser']=="UTEP","Texas-El Paso",games['Loser'])
games['Loser'] = np.where(games['Loser']=="UNC Asheville","North Carolina-Asheville",games['Loser'])
games['Loser'] = np.where(games['Loser']=="UNC Greensboro","North Carolina-Greensboro",games['Loser'])
games['Loser'] = np.where(games['Loser']=="UNC Wilmington","North Carolina-Wilmington",games['Loser'])
games['Loser'] = np.where(games['Loser']=="UNLV","Nevada-Las Vegas",games['Loser'])
games['Loser'] = np.where(games['Loser']=="SMU","Southern Methodist",games['Loser'])
games['Loser'] = np.where(games['Loser']=="LIU","Long Island University",games['Loser'])
games['Loser'] = np.where(games['Loser']=="NC State","North Carolina State",games['Loser'])
games['Loser'] = np.where(games['Loser']=="UCF","Central Florida",games['Loser'])
games['Loser'] = np.where(games['Loser']=="Southern Miss","Southern Mississippi",games['Loser'])
games['Loser'] = np.where(games['Loser']=="LSU","Louisiana State",games['Loser'])
games['Loser'] = np.where(games['Loser']=="UIC","Illinois-Chicago",games['Loser'])
games['Loser'] = np.where(games['Loser']=="UMBC","Maryland-Baltimore County",games['Loser'])

In [112]:
games['Home'] = np.where(games['Home']=="Ole Miss","Mississippi",games['Home'])
games['Home'] = np.where(games['Home']=="UCSB","UC-Santa Barbara",games['Home'])
games['Home'] = np.where(games['Home']=="UMass-Lowell","Massachusetts-Lowell",games['Home'])
games['Home'] = np.where(games['Home']=="UMass","Massachusetts",games['Home'])
games['Home'] = np.where(games['Home']=="UIC","Illinois-Chicago",games['Home'])
games['Home'] = np.where(games['Home']=="UConn","Connecticut",games['Home'])
games['Home'] = np.where(games['Home']=="Saint Mary's","Saint Mary's (CA)",games['Home'])
games['Home'] = np.where(games['Home']=="VCU","Virginia Commonwealth",games['Home'])
games['Home'] = np.where(games['Home']=="UMKC","Missouri-Kansas City",games['Home'])
games['Home'] = np.where(games['Home']=="St. Joseph's","Saint Joseph's",games['Home'])
games['Home'] = np.where(games['Home']=="BYU","Brigham Young",games['Home'])
games['Home'] = np.where(games['Home']=="UNC","North Carolina",games['Home'])
games['Home'] = np.where(games['Home']=="UTSA","Texas-San Antonio",games['Home'])
games['Home'] = np.where(games['Home']=="Pitt","Pittsburgh",games['Home'])
games['Home'] = np.where(games['Home']=="ETSU","East Tennessee State",games['Home'])
games['Home'] = np.where(games['Home']=="UT-Martin","Tennessee-Martin",games['Home'])
games['Home'] = np.where(games['Home']=="Penn","Pennsylvania",games['Home'])
games['Home'] = np.where(games['Home']=="California","University of California",games['Home'])
games['Home'] = np.where(games['Home']=="USC","Southern California",games['Home'])
games['Home'] = np.where(games['Home']=="UTEP","Texas-El Paso",games['Home'])
games['Home'] = np.where(games['Home']=="UNC Asheville","North Carolina-Asheville",games['Home'])
games['Home'] = np.where(games['Home']=="UNC Greensboro","North Carolina-Greensboro",games['Home'])
games['Home'] = np.where(games['Home']=="UNC Wilmington","North Carolina-Wilmington",games['Home'])
games['Home'] = np.where(games['Home']=="UNLV","Nevada-Las Vegas",games['Home'])
games['Home'] = np.where(games['Home']=="SMU","Southern Methodist",games['Home'])
games['Home'] = np.where(games['Home']=="LIU","Long Island University",games['Home'])
games['Home'] = np.where(games['Home']=="NC State","North Carolina State",games['Home'])
games['Home'] = np.where(games['Home']=="UCF","Central Florida",games['Home'])
games['Home'] = np.where(games['Home']=="Southern Miss","Southern Mississippi",games['Home'])
games['Home'] = np.where(games['Home']=="LSU","Louisiana State",games['Home'])
games['Home'] = np.where(games['Home']=="UIC","Illinois-Chicago",games['Home'])
games['Home'] = np.where(games['Home']=="UMBC","Maryland-Baltimore County",games['Home'])

In [113]:
games['Away'] = np.where(games['Away']=="Ole Miss","Mississippi",games['Away'])
games['Away'] = np.where(games['Away']=="UCSB","UC-Santa Barbara",games['Away'])
games['Away'] = np.where(games['Away']=="UMass-Lowell","Massachusetts-Lowell",games['Away'])
games['Away'] = np.where(games['Away']=="UMass","Massachusetts",games['Away'])
games['Away'] = np.where(games['Away']=="UIC","Illinois-Chicago",games['Away'])
games['Away'] = np.where(games['Away']=="UConn","Connecticut",games['Away'])
games['Away'] = np.where(games['Away']=="Saint Mary's","Saint Mary's (CA)",games['Away'])
games['Away'] = np.where(games['Away']=="VCU","Virginia Commonwealth",games['Away'])
games['Away'] = np.where(games['Away']=="UMKC","Missouri-Kansas City",games['Away'])
games['Away'] = np.where(games['Away']=="St. Joseph's","Saint Joseph's",games['Away'])
games['Away'] = np.where(games['Away']=="BYU","Brigham Young",games['Away'])
games['Away'] = np.where(games['Away']=="UNC","North Carolina",games['Away'])
games['Away'] = np.where(games['Away']=="UTSA","Texas-San Antonio",games['Away'])
games['Away'] = np.where(games['Away']=="Pitt","Pittsburgh",games['Away'])
games['Away'] = np.where(games['Away']=="ETSU","East Tennessee State",games['Away'])
games['Away'] = np.where(games['Away']=="UT-Martin","Tennessee-Martin",games['Away'])
games['Away'] = np.where(games['Away']=="Penn","Pennsylvania",games['Away'])
games['Away'] = np.where(games['Away']=="California","University of California",games['Away'])
games['Away'] = np.where(games['Away']=="USC","Southern California",games['Away'])
games['Away'] = np.where(games['Away']=="UTEP","Texas-El Paso",games['Away'])
games['Away'] = np.where(games['Away']=="UNC Asheville","North Carolina-Asheville",games['Away'])
games['Away'] = np.where(games['Away']=="UNC Greensboro","North Carolina-Greensboro",games['Away'])
games['Away'] = np.where(games['Away']=="UNC Wilmington","North Carolina-Wilmington",games['Away'])
games['Away'] = np.where(games['Away']=="UNLV","Nevada-Las Vegas",games['Away'])
games['Away'] = np.where(games['Away']=="SMU","Southern Methodist",games['Away'])
games['Away'] = np.where(games['Away']=="LIU","Long Island University",games['Away'])
games['Away'] = np.where(games['Away']=="NC State","North Carolina State",games['Away'])
games['Away'] = np.where(games['Away']=="UCF","Central Florida",games['Away'])
games['Away'] = np.where(games['Away']=="Southern Miss","Southern Mississippi",games['Away'])
games['Away'] = np.where(games['Away']=="LSU","Louisiana State",games['Away'])
games['Away'] = np.where(games['Away']=="UIC","Illinois-Chicago",games['Away'])
games['Away'] = np.where(games['Away']=="UMBC","Maryland-Baltimore County",games['Away'])

In [114]:
games['WinnerHome'] = np.where(games['Winner']==games['Home'],1,0)

In [115]:
games

Date          Winner Win_Score                     Loser  \
0     2016-11-11            Duke        94                    Marist   
1     2016-11-11        Kentucky        87         Stephen F. Austin   
2     2016-11-11         Indiana       103                    Kansas   
3     2016-11-11       Villanova        88                 Lafayette   
4     2016-11-11          Oregon        91                      Army   
...          ...             ...       ...                       ...   
5530  2017-03-31         Wyoming        83          Coastal Carolina   
5531  2017-03-31     St. Peter's        62  Texas A&M-Corpus Christi   
5532  2017-04-01  North Carolina        77                    Oregon   
5533  2017-04-01         Gonzaga        77            South Carolina   
5534  2017-04-03  North Carolina        71                   Gonzaga   

     Lose_Score                      Home               Away  WinnerHome  
0            49                      Duke             Marist           1  
1            64                  Kentucky  Stephen F. Austin           1  
2            99                    Kansas            Indiana           0  
3            48                 Villanova          Lafayette           1  
4            77                    Oregon               Army           1  
...         ...                       ...                ...         ...  
5530         59                   Wyoming   Coastal Carolina           1  
5531         61  Texas A&M-Corpus Christi        St. Peter's           0  
5532         76            North Carolina             Oregon           1  
5533         73                   Gonzaga     South Carolina           1  
5534         65            North Carolina            Gonzaga           1  

[5535 rows x 8 columns]

In [116]:
latest_stats=latest_stats.drop(['record_date'], axis=1)

In [117]:
half_join_latest = games.merge(latest_stats,left_on=['Away'],right_on=['Team'],how='left')
full_join_latest = half_join_latest.merge(latest_stats,left_on=['Home'],right_on=['Team'],how='left',suffixes=('_Away','_Home'))
full_join_latest = full_join_latest.drop(['Winner','Loser','Team_Home','Team_Away'],axis = 1)

In [118]:
full_join_latest

Date Win_Score Lose_Score                      Home  \
0     2016-11-11        94         49                      Duke   
1     2016-11-11        87         64                  Kentucky   
2     2016-11-11       103         99                    Kansas   
3     2016-11-11        88         48                 Villanova   
4     2016-11-11        91         77                    Oregon   
...          ...       ...        ...                       ...   
5530  2017-03-31        83         59                   Wyoming   
5531  2017-03-31        62         61  Texas A&M-Corpus Christi   
5532  2017-04-01        77         76            North Carolina   
5533  2017-04-01        77         73                   Gonzaga   
5534  2017-04-03        71         65            North Carolina   

                   Away  WinnerHome  KenPomRank_Away KenPomVal_Away  \
0                Marist           1            312.0         -13.63   
1     Stephen F. Austin           1            233.0          -6.19   
2               Indiana           0             44.0         +14.49   
3             Lafayette           1            330.0         -16.79   
4                  Army           1            230.0          -6.04   
...                 ...         ...              ...            ...   
5530   Coastal Carolina           1            207.0          -3.56   
5531        St. Peter's           0              NaN            NaN   
5532             Oregon           1             10.0         +25.02   
5533     South Carolina           1             24.0         +20.80   
5534            Gonzaga           1              1.0         +32.05   

     BPIrank_Away BPIval_Away  ... d_eff_Home ppg_Home papg_Home Pace_Home  \
0             305        -8.0  ...      91.17     80.8      70.2      69.9   
1             262        -5.2  ...      86.87     84.9      71.5      74.3   
2              32        10.6  ...      89.65     83.2      71.9      71.4   
3             330       -10.9  ...      87.45     77.2      62.7      65.6   
4             253        -4.7  ...      88.20     78.9      65.8      68.8   
...           ...         ...  ...        ...      ...       ...       ...   
5530          218        -2.8  ...      98.47     77.9      74.6      74.0   
5531          NaN         NaN  ...     103.26     75.4      71.5      70.5   
5532           10        17.4  ...      86.92     84.4      70.6      72.6   
5533           28        11.4  ...      82.51     82.6      61.5      70.9   
5534            1        20.4  ...      86.92     84.4      70.6      72.6   

     Three_Par_Home True_Shoot_Home Tov_Home Opp_Three_Par_Home  \
0              .383            .588     14.2               .288   
1              .316            .564     13.4               .333   
2              .359            .583     15.1               .342   
3              .433            .612     15.0               .400   
4              .388            .582     14.7               .378   
...             ...             ...      ...                ...   
5530           .466            .555     15.8               .348   
5531           .284            .555     16.5               .415   
5532           .303            .550     13.4               .395   
5533           .329            .596     14.2               .321   
5534           .303            .550     13.4               .395   

     Opp_True_Shoot_Home Opp_Tov_Home  
0                   .510         14.9  
1                   .507         16.9  
2                   .515         16.1  
3                   .506         17.6  
4                   .494         16.6  
...                  ...          ...  
5530                .503         14.0  
5531                .543         19.9  
5532                .517         16.6  
5533                .443         14.9  
5534                .517         16.6  

[5535 rows x 40 columns]

In [119]:
full_join_latest.to_csv('season1617.csv')